In [1]:
/**
 The following notebook does:
     - Reads a single- or a multi- band GeoTiff from HDFS
     - Filters out or converts NaN values
     - Runs Kmeans
     - Saves the kmeans model to HDFS
**/


import geotrellis.raster.MultibandTile
import geotrellis.spark.io.hadoop._
import geotrellis.vector.ProjectedExtent
import org.apache.hadoop.fs.Path
import org.apache.spark.{SparkConf, SparkContext}
import org.apache.spark.mllib.clustering.KMeans
import org.apache.spark.mllib.linalg.Vectors
import org.apache.spark.rdd.RDD

In [14]:
var band_NaN_RDD :RDD[Array[Double]] = sc.emptyRDD

//The following example shows how to get the number of bands, however, it is not known 
//val band_count = geotrellis.raster.io.geotiff.reader.TiffTagsReader.read(filepath).bandCount;

val band_count = 4;
var filepath :String = ""
if (band_count == 1) {
    //Single band GeoTiff
    filepath = "hdfs:///user/hadoop/spring-index/LastFreeze/1980.tif"
} else {
    //Multi band GeoTiff
    filepath = "hdfs:///user/hadoop/spring-index/BloomFinal/1980.tif"
}
    
if (band_count == 1) {
    //Lets load a Singleband GeoTiff and return RDD just with the tiles.
    //Since it is a single GeoTiff, it will be a RDD with a tile.
    val bands_RDD = sc.hadoopGeoTiffRDD(filepath).values
    band_NaN_RDD = bands_RDD.map( m => m.toArrayDouble())
} else {
    //Lets load a Multiband GeoTiff and return RDD just with the tiles.
    //Since it is a single GeoTiff, it will be a RDD with a tile.
    val bands_RDD = sc.hadoopMultibandGeoTiffRDD(filepath).values
    
    //Extract the 4th band
    band_NaN_RDD = bands_RDD.map( m => m.band(3).toArrayDouble())
}

//Go to each vector and print the length of each vector
band_NaN_RDD.collect().foreach(m => println("vector length with NaN is %d".format(m.length)))

//Go to each vector and filter out all NaN values
val band_RDD = band_NaN_RDD.map(m => m.filter(v => !v.isNaN))

//Go to each vector and print the length of each vector
band_RDD.collect().foreach(m => println("vector length without NaN is %d".format(m.length)))

vector length with NaN is 30388736
vector length without NaN is 13695035


In [15]:
// Create a Vector with NaN converted to 0s
//val band_vec = band_NaN_RDD.map(s => Vectors.dense(s.map(v => if (v.isNaN) 0 else v))).cache()

// Create a Vector without NaN values
val band_vec = band_RDD.map(s => Vectors.dense(s)).cache()

In [16]:
val numClusters = 2
val numIterations = 20
val clusters = {
    KMeans.train(band_vec,numClusters,numIterations)
}

// Evaluate clustering by computing Within Set Sum of Squared Errors
val WSSSE = clusters.computeCost(band_vec)
println("Within Set Sum of Squared Errors = " + WSSSE)

Within Set Sum of Squared Errors = 0.0


In [17]:
//Un-persist the model
band_vec.unpersist()

// Shows the result.
println("Cluster Centers: ")
clusters.clusterCenters.foreach(println)

//Clusters save the model
if (band_count == 1) {
    clusters.save(sc, "hdfs:///user/emma/spring_index/LastFreeze/1980_kmeans_model")    
} else {
    clusters.save(sc, "hdfs:///user/emma/spring_index/BloomFinal/1980_kmeans_model")
}


Cluster Centers: 


[116.0,116.0,116.0,116.0,124.0,141.0,141.0,153.0,153.0,151.0,119.0,119.0,117.0,135.0,149.0,149.0,148.0,118.0,117.0,117.0,123.0,153.0,159.0,159.0,161.0,161.0,131.0,138.0,138.0,151.0,151.0,153.0,157.0,157.0,149.0,149.0,134.0,154.0,154.0,152.0,152.0,158.0,153.0,153.0,149.0,149.0,145.0,154.0,154.0,159.0,159.0,153.0,155.0,149.0,149.0,150.0,135.0,133.0,133.0,144.0,157.0,154.0,163.0,163.0,162.0,158.0,158.0,156.0,156.0,158.0,158.0,158.0,162.0,162.0,160.0,149.0,149.0,159.0,159.0,153.0,149.0,149.0,145.0,147.0,151.0,151.0,150.0,156.0,154.0,154.0,154.0,147.0,147.0,129.0,127.0,127.0,126.0,126.0,125.0,127.0,127.0,126.0,126.0,127.0,126.0,126.0,126.0,126.0,126.0,130.0,130.0,128.0,128.0,127.0,127.0,127.0,123.0,123.0,123.0,125.0,126.0,126.0,127.0,131.0,130.0,130.0,132.0,139.0,139.0,140.0,140.0,141.0,137.0,137.0,137.0,137.0,149.0,154.0,154.0,154.0,154.0,153.0,151.0,151.0,149.0,151.0,147.0,148.0,148.0,145.0,146.0,144.0,139.0,139.0,135.0,135.0,136.0,132.0,132.0,130.0,130.0,129.0,129.0,127.0,127.0,126.0,127

5.0,155.0,129.0,129.0,122.0,123.0,123.0,138.0,138.0,160.0,163.0,135.0,140.0,163.0,163.0,173.0,173.0,163.0,155.0,155.0,138.0,138.0,126.0,123.0,123.0,136.0,136.0,142.0,154.0,154.0,163.0,163.0,138.0,147.0,147.0,164.0,168.0,168.0,149.0,149.0,143.0,142.0,142.0,140.0,140.0,133.0,130.0,130.0,124.0,124.0,122.0,121.0,119.0,118.0,118.0,118.0,119.0,119.0,125.0,137.0,137.0,155.0,155.0,166.0,162.0,162.0,167.0,167.0,155.0,160.0,160.0,153.0,155.0,158.0,162.0,162.0,163.0,166.0,166.0,154.0,162.0,161.0,168.0,168.0,168.0,168.0,162.0,167.0,167.0,173.0,173.0,169.0,168.0,168.0,177.0,171.0,171.0,173.0,173.0,170.0,165.0,155.0,148.0,148.0,143.0,138.0,138.0,143.0,145.0,155.0,148.0,148.0,133.0,129.0,129.0,143.0,143.0,140.0,136.0,136.0,136.0,136.0,129.0,127.0,127.0,131.0,131.0,136.0,137.0,139.0,140.0,142.0,142.0,142.0,142.0,143.0,149.0,149.0,158.0,158.0,158.0,149.0,149.0,142.0,142.0,138.0,140.0,140.0,139.0,139.0,138.0,143.0,143.0,148.0,154.0,154.0,161.0,161.0,173.0,167.0,167.0,163.0,163.0,158.0,164.0,159.0,154.0,

36.0,136.0,136.0,136.0,136.0,137.0,137.0,137.0,137.0,137.0,136.0,136.0,136.0,136.0,136.0,136.0,137.0,137.0,137.0,137.0,137.0,136.0,136.0,136.0,135.0,135.0,135.0,136.0,136.0,136.0,136.0,136.0,136.0,136.0,137.0,137.0,137.0,137.0,137.0,137.0,137.0,137.0,137.0,137.0,137.0,137.0,137.0,136.0,136.0,136.0,136.0,136.0,136.0,136.0,136.0,137.0,136.0,136.0,136.0,136.0,136.0,136.0,136.0,136.0,136.0,136.0,136.0,136.0,136.0,136.0,136.0,136.0,135.0,135.0,135.0,135.0,135.0,133.0,132.0,132.0,132.0,132.0,130.0,130.0,130.0,130.0,130.0,130.0,130.0,130.0,130.0,130.0,130.0,130.0,130.0,130.0,130.0,130.0,130.0,130.0,130.0,130.0,130.0,130.0,130.0,130.0,130.0,130.0,130.0,130.0,130.0,130.0,130.0,130.0,130.0,131.0,131.0,130.0,130.0,130.0,130.0,130.0,131.0,131.0,131.0,131.0,131.0,131.0,131.0,131.0,131.0,131.0,131.0,131.0,131.0,131.0,131.0,131.0,131.0,131.0,131.0,131.0,132.0,132.0,132.0,132.0,132.0,133.0,133.0,133.0,133.0,133.0,133.0,133.0,133.0,133.0,133.0,133.0,133.0,133.0,133.0,133.0,133.0,133.0,133.0,133.0,133.0

30.0,130.0,130.0,130.0,130.0,130.0,129.0,129.0,129.0,129.0,129.0,129.0,129.0,129.0,129.0,129.0,129.0,129.0,129.0,129.0,129.0,129.0,129.0,129.0,129.0,129.0,129.0,129.0,129.0,129.0,129.0,129.0,129.0,129.0,129.0,129.0,129.0,129.0,129.0,129.0,129.0,129.0,129.0,129.0,129.0,129.0,129.0,129.0,129.0,129.0,129.0,129.0,129.0,129.0,129.0,129.0,129.0,129.0,129.0,129.0,129.0,129.0,129.0,129.0,128.0,128.0,128.0,128.0,128.0,129.0,129.0,129.0,129.0,129.0,128.0,128.0,128.0,128.0,128.0,129.0,129.0,129.0,128.0,128.0,128.0,128.0,128.0,128.0,128.0,128.0,128.0,128.0,128.0,128.0,128.0,128.0,128.0,128.0,128.0,128.0,128.0,128.0,128.0,128.0,128.0,128.0,128.0,128.0,128.0,128.0,128.0,128.0,128.0,128.0,128.0,128.0,128.0,128.0,128.0,128.0,128.0,128.0,128.0,128.0,128.0,128.0,128.0,128.0,128.0,128.0,128.0,128.0,128.0,127.0,127.0,126.0,126.0,126.0,126.0,127.0,127.0,128.0,128.0,128.0,129.0,129.0,126.0,126.0,126.0,126.0,126.0,126.0,126.0,126.0,126.0,126.0,126.0,126.0,126.0,126.0,126.0,126.0,126.0,126.0,126.0,126.0,126.0

...

0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,54.0,53.0,54.0,54.0,54.0,54.0,54.0,54.0,53.0,53.0,53.0,54.0,54.0,54.0,54.0,53.0,53.0,54.0,54.0,54.0,54.0,54.0,53.0,53.0,53.0,53.0,53.0,53.0,53.0,53.0,53.0,53.0,53.0,53.0,53.0,53.0,53.0,53.0,53.0,53.0,53.0,53.0,53.0,53.0,53.0,53.0,53.0,53.0,53.0,53.0,53.0,53.0,53.0,53.0,53.0,53.0,53.0,53.0,53.0,53.0,53.0,53.0,53.0,53.0,53.0,53.0,53.0,53.0,53.0,53.0,53.0,53.0,53.0,53.0,53.0,53.0,53.0,53.0,53.0,53.0,53.0,53.0,53.0,53.0,53.0,53.0,53.0,53.0,53.0,53.0,53.0,53.0,53.0,53.0,53.0,53.0,53.0,53.0,53.0,53.0,53.0,53.0,53.0,53.0,53.0,53.0,53.0,53.

2.0,52.0,52.0,52.0,52.0,52.0,52.0,52.0,52.0,52.0,52.0,52.0,52.0,52.0,52.0,52.0,52.0,52.0,52.0,52.0,51.0,51.0,51.0,52.0,52.0,52.0,51.0,51.0,52.0,52.0,52.0,52.0,51.0,51.0,51.0,52.0,52.0,52.0,52.0,52.0,52.0,52.0,52.0,52.0,52.0,52.0,52.0,52.0,52.0,52.0,52.0,52.0,52.0,52.0,52.0,52.0,52.0,52.0,52.0,51.0,51.0,51.0,51.0,51.0,51.0,51.0,51.0,51.0,51.0,51.0,51.0,51.0,51.0,51.0,51.0,51.0,51.0,51.0,51.0,51.0,51.0,51.0,51.0,52.0,52.0,52.0,51.0,52.0,52.0,52.0,51.0,51.0,51.0,51.0,51.0,51.0,51.0,51.0,51.0,51.0,51.0,51.0,51.0,51.0,52.0,52.0,52.0,51.0,51.0,52.0,51.0,51.0,51.0,51.0,51.0,52.0,52.0,52.0,51.0,51.0,51.0,51.0,51.0,51.0,51.0,51.0,51.0,51.0,51.0,51.0,51.0,51.0,51.0,51.0,51.0,51.0,51.0,52.0,51.0,51.0,52.0,52.0,52.0,52.0,51.0,51.0,51.0,51.0,51.0,51.0,51.0,51.0,51.0,51.0,50.0,50.0,50.0,50.0,50.0,50.0,50.0,51.0,51.0,51.0,50.0,50.0,50.0,50.0,50.0,50.0,50.0,51.0,51.0,51.0,51.0,50.0,51.0,51.0,49.0,49.0,49.0,49.0,49.0,49.0,49.0,50.0,50.0,50.0,50.0,50.0,50.0,50.0,50.0,50.0,50.0,50.0,50.0,50.0,50.0,50.0,5

.0,133.0,133.0,137.0,139.0,142.0,135.0,124.0,121.0,121.0,114.0,115.0,115.0,116.0,109.0,109.0,96.0,99.0,97.0,91.0,88.0,83.0,83.0,83.0,81.0,82.0,79.0,74.0,74.0,75.0,85.0,83.0,82.0,83.0,90.0,90.0,103.0,100.0,101.0,104.0,103.0,103.0,101.0,99.0,96.0,98.0,99.0,102.0,102.0,101.0,100.0,99.0,97.0,98.0,98.0,96.0,95.0,95.0,93.0,95.0,95.0,96.0,94.0,93.0,81.0,71.0,68.0,68.0,68.0,69.0,66.0,65.0,65.0,64.0,65.0,64.0,64.0,64.0,63.0,63.0,63.0,63.0,63.0,63.0,63.0,63.0,63.0,63.0,63.0,63.0,63.0,63.0,64.0,64.0,64.0,65.0,66.0,67.0,67.0,67.0,67.0,68.0,66.0,64.0,63.0,63.0,63.0,61.0,61.0,61.0,61.0,61.0,61.0,61.0,61.0,61.0,61.0,61.0,61.0,61.0,60.0,60.0,61.0,61.0,62.0,62.0,63.0,63.0,64.0,63.0,60.0,60.0,60.0,60.0,59.0,59.0,60.0,59.0,59.0,59.0,59.0,60.0,60.0,60.0,60.0,60.0,60.0,60.0,60.0,60.0,60.0,60.0,60.0,61.0,63.0,68.0,69.0,61.0,61.0,60.0,59.0,59.0,59.0,60.0,60.0,60.0,60.0,60.0,60.0,60.0,60.0,60.0,60.0,62.0,63.0,63.0,64.0,64.0,64.0,64.0,64.0,64.0,64.0,64.0,64.0,64.0,66.0,68.0,70.0,70.0,70.0,70.0,71.0,71.0,71.0,7

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.


[Stage 45:=============================>                            (1 + 1) / 2]